In [1]:
import numpy as np
import napari
import SimpleITK as sitk
import nd2

In [8]:
!python -V

# 3.7 works with ND2Reader, need to set to 3.7 then re-make the Elastix

Python 3.10.2


In [7]:
# ND2Reader not compatible with Python 3

from nd2reader import ND2Reader

ImportError: cannot import name 'Iterable' from 'collections' (/home/ebesier/miniconda3/envs/exm-toolbox/lib/python3.10/collections/__init__.py)

In [5]:
# Read in data. Round 1 to Round 4 are images of 12 RNAs using HCR-FISH, 
# Round 5 to Round 7 are images of proteins using antibody staining. 
# We want to align rounds of images using the 405 channel (index 0), and register to Round 1.
# We will perform segmentation later. 

In [6]:
f_vol_1 = './Stress_granule/Round1.nd2'
f_vol_2 = './Stress_granule/Round2.nd2'

In [7]:
a_vol_1 = nd2.imread(f_vol_1, sitk.sitkFloat32)
a_vol_2 = nd2.imread(f_vol_2, sitk.sitkFloat32)

In [8]:
a_vol_1

dask.array<_dask_block, shape=(60, 4, 2048, 2048), dtype=uint16, chunksize=(1, 4, 2048, 2048), chunktype=numpy.ndarray>

In [9]:
a_vol_2

dask.array<_dask_block, shape=(74, 4, 2048, 2048), dtype=uint16, chunksize=(1, 4, 2048, 2048), chunktype=numpy.ndarray>

In [10]:
channel = 0
a_vol_1[:, channel, :, :].shape

(60, 2048, 2048)

In [11]:
a_vol_2[:, channel, :, :].shape

(74, 2048, 2048)

In [31]:
channel = 0
aligned_images = []

for chunk in np.arange(a_vol_1[:, channel, :, :].shape[0]):
    chunk_vol_1 = sitk.GetImageFromArray(a_vol_1[chunk, channel, :, :], sitk.sitkFloat32)
    chunk_vol_2 = sitk.GetImageFromArray(a_vol_2[chunk, channel, :, :], sitk.sitkFloat32)
    
    selectCastFilter = sitk.VectorIndexSelectionCastImageFilter()
    selectCastFilter.SetIndex(0)
    selectCastFilter.SetOutputPixelType(sitk.sitkFloat32)
    chunk_vol_1 = selectCastFilter.Execute(chunk_vol_1)
    chunk_vol_2 = selectCastFilter.Execute(chunk_vol_2)
    
    elastixImageFilter = sitk.ElastixImageFilter()

    # Set fixed image to be Round 1
    elastixImageFilter.SetFixedImage(chunk_vol_1)

    # Set fixed image to be Round 2
    elastixImageFilter.SetMovingImage(chunk_vol_2)

    # Set filter to shearing, scaling, rotation and translation. Need to do segmentation later.
    elastixImageFilter.SetParameterMap(sitk.GetDefaultParameterMap("affine"))
    elastixImageFilter.Execute()

    # Save output
    param_map = elastixImageFilter.GetTransformParameterMap()[0]
    sitk.WriteParameterFile(param_map, 'param_map' + '.txt')
    result_img = sitk.GetArrayFromImage(elastixImageFilter.GetResultImage())
    aligned_images.append(result_img)

Time spent on saving the results, applying the final transform etc.: 485 ms.
ELASTIX version: 5.000
Command line options from ElastixBase:
-fMask    unspecified, so no fixed mask used
-mMask    unspecified, so no moving mask used
-out      ./
-threads  unspecified, so all available threads are used
  The default value "true" is used instead.

  From elastix 4.8 it defaults to true!
This may change the behavior of your registrations considerably.

Command line options from TransformBase:
-t0       unspecified, so no initial transform used

Reading images...
Reading images took 0 ms.

  A default pyramid schedule is used.
  A default pyramid schedule is used.
  The default value "false" is used instead.
  The default value "GeometricalCenter" is used instead.
Transform parameters are initialized as: [1, 0, 0, 1, 0, 0]
InitializeTransform took 0.00s
Scales are estimated automatically.
Scales for transform parameters are: [353600.25, 353600.25, 353600.25, 353600.25, 1, 1]
Initialization of

In [33]:
aligned_images = np.array(aligned_images)
aligned_images.shape

(60, 2048, 2048)

In [13]:
import napari

In [ ]:
# Napari crashes kernel -- display works locally but not on cluster

viewer = napari.Viewer()
#new_layer = viewer.add_image(nd2.imread(f_vol_out), rgb=True)